In [2]:
!pip install praw

     |████████████████████████████████| 188 kB 5.4 MB/s eta 0:00:01


In [30]:
from praw import reddit
import json
import time
import ipfshttpclient
from os import listdir
from os.path import isfile, join
import re
import praw

import substrateinterface
from substrateinterface import SubstrateInterface, Keypair
from substrateinterface.exceptions import SubstrateRequestException

In [328]:
reddit = praw.Reddit(
    client_id="LtjnfEAH_rRdFDbMwILwxw",
    client_secret="04WSBZHCzqm0ElLYMRkmTkmijCCSog",
    password="PosterThreading69",
    user_agent="my user agent",
    username="postthreadbot",
)

In [3]:
subreddits = "announcements+Art+AskReddit+askscience+atheism+aww+blog+books+creepy+dataisbeautiful+DIY+Documentaries+EarthPorn+explainlikeimfive+food+funny+Futurology+gadgets+gaming+GetMotivated+gifs+history+IAmA+InternetIsBeautiful+Jokes+LifeProTips+listentothis+mildlyinteresting+movies+Music+news+nosleep+nottheonion+OldSchoolCool+personalfinance+philosophy+photoshopbattles+pics+science+Showerthoughts+space+sports+television+tifu+todayilearned+TwoXChromosomes+UpliftingNews+videos+worldnews+WritingPrompts"

In [4]:
substrate = SubstrateInterface(
    url="ws://127.0.0.1:11946",
    ss58_format=42,
    type_registry_preset='kusama'
)

In [61]:
# Function to make extrinsic calls
def make_call(call_module, call_function, call_params, keypair, wait_for_inclusion=True, wait_for_finalization=False):
    call = substrate.compose_call(
        call_module=call_module,  
        call_function=call_function,
        call_params=call_params
    )

    extrinsic = substrate.create_signed_extrinsic(call=call, keypair=keypair)

    try:
        receipt = substrate.submit_extrinsic(extrinsic, wait_for_inclusion=wait_for_inclusion, wait_for_finalization=wait_for_finalization)
        print("Extrinsic '{}' sent and included in block '{}'".format(receipt.extrinsic_hash, receipt.block_hash))

    except SubstrateRequestException as e:
        print("Failed to send: {}".format(e))
    return receipt

In [243]:
def addSchema(schema, check=True, create=True):
    schemaId = None
    if check:
        schema_count = substrate.query(
            module='Schemas',
            storage_function='SchemaCount',
            params=[]
        ).value

        for i in range(1, schema_count+1):
            schemaTemp = substrate.query(
                module='Schemas',
                storage_function='Schemas',
                params=[i]
            )
            if schemaTemp == schema:
                schemaId = i
                return schemaId

    if schemaId is None and create:
        receipt = make_call("Schemas", "register_schema", {"schema": schema}, bob)
        for event in receipt.triggered_events:
            event = event.decode()
            if event['event']['module_id'] == 'SchemaRegistered':
                schemaId = event['event']['attributes'][1]
                return schemaId
       
        # didn't find msa in events so call function to check for msa
        while (schemaId is None):
            schemaId = addSchema(schema, check=True, create=False)
        return schemaId

In [212]:
def get_msa_id(wallet, create=True, wait_for_inclusion=True, wait_for_finalization=False):
    msa_key = substrate.query(
        module='Msa',
        storage_function='KeyInfoOf',
        params=[wallet.ss58_address]
    )
    
    if not create:
        return None

    if msa_key == None:
        make_call("Msa", "create", {}, wallet, wait_for_inclusion=wait_for_inclusion, wait_for_finalization=wait_for_finalization)
        msa_key = substrate.query(
            module='Msa',
            storage_function='KeyInfoOf',
            params=[wallet.ss58_address]
        )

    msa_id = msa_key['msa_id'].decode()
    return msa_id

In [9]:
def get_signature(payload, signer):
    # encode payload using SCALE
    # I found scale_info from "substrate.metadata_decoder"
    payload_encoded = substrate.encode_scale(type_string='scale_info::8', value=payload['authorized_msa_id']) + \
                            substrate.encode_scale(type_string='scale_info::2', value=payload['permission'])

    # Payload must be wrapped in theses Bytes objects
    payload_encoded = "<Bytes>".encode() + payload_encoded.data + "</Bytes>".encode()

    # The provider address signs the payload, so in this case alice
    return signer.sign(payload_encoded)

In [204]:
def create_msa_with_delegator(provider_wallet, delegator_wallet):    
    provider_msa_id = get_msa_id(provider_wallet)

    payload_raw = { "authorized_msa_id": provider_msa_id, "permission": 0 }

    signature = get_signature(payload_raw, delegator_wallet)

    call_params = {
        "delegator_key": delegator_wallet.ss58_address,
        "proof": {"Sr25519": "0x" + signature.hex()},
        "add_provider_payload": payload_raw
    }

    # provider signs this
    receipt = make_call("Msa", "create_sponsored_account_with_delegation", call_params, provider_wallet)
    for event in receipt.triggered_events:
        event = event.decode()
        if event['event']['module_id'] == 'Msa':
            msa_id = event['event']['attributes'][0]
            return msa_id

In [65]:
def get_data(announcement):
    data = f"{str(announcement.subreddit)},{str(announcement.author.name)},{str(announcement.title)},{str(announcement.selftext)},{str(announcement.url)},{announcement.over_18}"
#     data_hash = substrateinterface.utils.hasher.xxh128(data)
    return data

In [514]:
def mint_votes(user_msa_id, announcement, parent_hash, _schemaId):
    receipt_ups = None
    receipt_downs = None
    extra_comma = ',' if _schemaId == postvote_schemaId else ''
    print(extra_comma)
    
    if announcement.ups > 0:
        call_params = {
            "on_behalf_of": user_msa_id,
            "schema_id": _schemaId,
            "message": f",{extra_comma}{parent_hash},{announcement.ups}"
        }
        receipt_ups = make_call("Messages", "add", call_params, bob, wait_for_inclusion=False, wait_for_finalization=False)
    
    if announcement.downs > 0:
        call_params = {
            "on_behalf_of": user_msa_id,
            "schema_id": _schemaId,
            "message": f",{extra_comma}{parent_hash},-{announcement.downs}"
        }
        receipt_downs = make_call("Messages", "add", call_params, bob, wait_for_inclusion=False, wait_for_finalization=False)
    
    return receipt_ups, receipt_downs

In [483]:
def mint_user(user):  
    # create a wallet for user and check if they have an msa id yet
    user_wallet = Keypair.create_from_uri('//' + user.name)
    user_msa_id = get_msa_id(user_wallet, create=False)
    
    # if not then add a user using the schema
    if user_msa_id is None:
        user_msa_id = create_msa_with_delegator(bob, user_wallet)
        user_data = f"{user.name},{user.icon_img}"
        schema = f"username,profile_pic"
        schemaId = addSchema(schema)
        
        call_params = {
            "on_behalf_of": user_msa_id,
            "schema_id": schemaId,
            "message": user_data
        }
        receipt_user = make_call("Messages", "add", call_params, bob, wait_for_inclusion=False, wait_for_finalization=False)
    return user_msa_id

In [484]:
def mint_comments(comments, post, post_data_hash):
    id_to_hash = {}
    for comment in comments:
        try:
#             comment_user_msa_id = mint_user(comment.author)
            comment_user_msa_id = None
            username = post.author.name
            profile_pic = post.author.icon_img
        except:
            comment_user_msa_id = None
            username = "removed"
            profile_pic = "removed"
               
        comment_data = {
            "parent_hash": post_data_hash,
            "username": username,
            "profile_pic": profile_pic,
            "body": comment.body,
        }
        json.dump(comment_data, open(f"./comments/{comment.name}.json", "w"))
        res_comment = client.add(f"./comments/{comment.name}.json")
        comment_data_hash = res_comment['Hash']
        if comment.parent_id == post.name:
            parent_hash = post_data_hash
            comment_schemaId = postcomment_schemaId
        else:
            parent_hash = id_to_hash[comment.parent_id]
            comment_schemaId = commentcomment_schemaId
            
        id_to_hash[comment.id] = comment_data_hash
        message_comment = f",{parent_hash},{comment_data_hash}"
            
        call_params = {
            "on_behalf_of": None,
            "schema_id": comment_schemaId,
            "message": message_comment
        }
        receipt_comment = make_call("Messages", "add", call_params, bob, wait_for_inclusion=False, wait_for_finalization=False)
        print(comment_data_hash)
        
        ## comment votes ##
        receipt_ups, receipt_downs = mint_votes(None, comment, comment_data_hash, commentvote_schemaId)
        print(comment.ups, comment.downs)

In [6]:
bob = Keypair.create_from_uri('//Bob')

In [329]:
r_all = reddit.subreddit('all')

In [340]:
r_all.top(time_filter='day')

In [335]:
reddit.front.top()

In [68]:
client = ipfshttpclient.connect()

/home/chia/miniconda3/lib/python3.8/site-packages/ipfshttpclient/client/__init__.py:73: VersionMismatch: Unsupported daemon version '0.13.0' (not in range: 0.5.0 ≤ … < 0.9.0)
  warnings.warn(exceptions.VersionMismatch(version, minimum, maximum))


In [507]:
schema = f"post,category,data_hash"
post_schemaId = addSchema(schema)

schema = f"postcomment,parent_hash,data_hash"
postcomment_schemaId = addSchema(schema)

schema = f"commentcomment,parent_hash,data_hash"
commentcomment_schemaId = addSchema(schema)

schema = f"postvote,category,parent_hash,votes"
postvote_schemaId = addSchema(schema)

schema = f"commentvote,parent_hash,votes"
commentvote_schemaId = addSchema(schema)

Extrinsic '0x4068514818a86045779bca050f3c6a4c1fa75b44590c0064038bea725d84d23d' sent and included in block '0xdc067595e48532a43b69935b565b1c920e63308131de5184a9b0c349c9551081'


In [ ]:
while (True):
    for i, post in enumerate(r_all.top(time_filter='day')):
        ## USER ##
        try:
#             user_msa_id = mint_user(post.author)
            user_msa_id = None
            username = post.author.name
            profile_pic = post.author.icon_img
        except:
            user_msa_id = None
            username = "removed"
            profile_pic = "removed"

        ## POST ##
        post_data = {
            "category": post.subreddit.display_name,
            "username": username,
            "profile_pic": profile_pic,
            "title": post.title,
            "body": post.selftext,
            "url": post.url,
            "is_nsfw": post.over_18
        }

        # use hash to check if we already added this post to the blockchain
        # if so then skip
        data_files = [f for f in listdir("./posts") if isfile(join("./posts", f))]
#         if f"{post.name}.json" in data_files:
#             continue

        json.dump(post_data, open(f"./posts/{post.name}.json", "w"))
        res_post = client.add(f"./posts/{post.name}.json")
        post_data_hash = res_post["Hash"]

        # create a schema for all children to use that includes post_hash in order to make easier querying
        # Note: post's will always have parent_hash as null, comments on posts will always have parent_hash as
        # post_data_hash and comments on comments will have their parent comment_data_hash as parent_hash
#         schema = f"{post.subreddit},{post_data_hash},parent_hash,data_hash"
#         schema = f"post,category,parent_hash,data_hash"
#         schemaId = addSchema(schema)

        call_params = {
            "on_behalf_of": None,
            "schema_id": post_schemaId,
            "message": f",{post.subreddit},{post_data_hash}"
        }
        receipt_post = make_call("Messages", "add", call_params, bob, wait_for_inclusion=False, wait_for_finalization=False)
        print(post_data_hash)

        ## post votes ##
        receipt_ups, receipt_downs = mint_votes(None, post, post_data_hash, postvote_schemaId)
        print(post.ups, post.downs)

        ## COMMENT ##
        mint_comments(post.comments.list()[:10], post, post_data_hash)
    #     head_comments = []
    #     for comment in post.comments.list():
    #         if comment.parent_id == post_data_hash:
    #             head_comments[comment].append(comment)
        
    print("waiting...")
    print()
    # sleep for a bit and then check again
    time.sleep(60*10)

Extrinsic '0xa048cbb5e88bb06e7ee3513a0236c8b6c61fbfc131ebd85c927a27a34cf01f29' sent and included in block 'None'
QmW1dkENpgN293WPhU79Y9VEAKmh8joYb2HRpDPwaVpfq2
,
Extrinsic '0xb7073b7d975576654e4db04b58ca030f7ce94184cd6828767d21889ec25bf26e' sent and included in block 'None'
131481 0
Extrinsic '0x2e215643510abaaebc38062932df7040de640b04343ab131e9ff59a80d54574b' sent and included in block 'None'
QmSKie1ThhqYwfXkMQBp5uL1TdQq3WEFx1FshSnjERmHdD

Extrinsic '0x08589e3002d0860ee453c1765131cb9118fe2b864c86726c03469e636095e5e9' sent and included in block 'None'
6618 0
Extrinsic '0x9586347fb6306e83e8e61c6f2b46e485c047b2dd4b3fc8e0f6e18d5b36666b29' sent and included in block 'None'
QmZG3LvaCbTMsCm5Q2iQNVHGqXM6ds6SzQygbi8efbW22p

Extrinsic '0x17e30b4d942c6729ebed9b11d37602a8cf69e2346abcf53f5b269f9b1d49605a' sent and included in block 'None'
7438 0
Extrinsic '0x0465c90e9a6bca6080a5a8d34155c6ba0c7b3ca05b9a34efff256d4fe08ee778' sent and included in block 'None'
QmckHq7EgpSX52wYDZymH2BcyqJPxFKsomshaP8WP

Extrinsic '0x3059a754d1ce0e0542eceb7fd3ee2688851637740fbbee680365ec193c7018f4' sent and included in block 'None'
QmfBGsDABqRZJ7FnPWodNkXsKEi4kg1oJbfPK83Xq6wQEF
,
Extrinsic '0xc823d0a3786fa63c981511a70a887d2cac3d667fb495013401bb108bd8b251ce' sent and included in block 'None'
76830 0
Extrinsic '0xb39bf3b678fc234a72481014bf23b55fbf5c2ca9ea213303fb4142bd59d03e43' sent and included in block 'None'
Qmetk46HCBsNgzeA8hNitFnUPVtXXwuK2JfzZ8arAVH4aD

Extrinsic '0xaa0032a7c6b0f698bd551f657de4495b56d4655848ca0b60633fdbfaaf0e4c24' sent and included in block 'None'
1 0
Extrinsic '0xe625417c1ceb741df6e9ca68799934a67f0dbbca363e628c12b654a83cf84849' sent and included in block 'None'
QmW6hiZAmxCQGV1V7gG72b4q3qBrVTsZNgPnALcrfCNcVM

Extrinsic '0xb682c6b30eccebb13c6f2595ae79041db05f27c7dce3345dd33095dbfd45a7de' sent and included in block 'None'
1153 0
Extrinsic '0xc0a3adaf2db56841c3714ab36c11fa7db943e371450b484359301d9b9e243ce8' sent and included in block 'None'
QmVUAa1CZRkkfnaDHxs4Q8MPsXBNdutb42QrTu2nFYxTt

Extrinsic '0x585a5b1a9e639805f695affb73d53e318933348a983a8efacf380c71f176bc60' sent and included in block 'None'
QmWVmW4Ti56hbuTScbMrbNuTgUZXyDXz91GTfCHhtHT27A
,
Extrinsic '0x07ae915949d9eb0f34336d894c03210e9f6d73aa8f8f685d4a1174a1198fb859' sent and included in block 'None'
66897 0
Extrinsic '0x09c9080d34ae4d93c876b573c8239eba7f121f7fd9ddda0cc2591893540effb5' sent and included in block 'None'
QmY4CjggKeAxsy5diGbjbwKyFmiKb6DqxvSkL5huTaFtWz

Extrinsic '0x04f88c13b19af61c8d5bc2ae21595d59cd409e17cb6504d2c72d3715388e18fa' sent and included in block 'None'
1223 0
Extrinsic '0x9fa2d86c3451a4edf563f9d89996f187f5aa19bae0b29ab9d50b10f5980bb0a3' sent and included in block 'None'
QmNsft7hQfXGs2Jf8XjTgAfA7YqBzXPcMkVaB2LJ7RySzK

Extrinsic '0x790240bcfc42e721f2dfee1f502089bc23f8cfbf7f3886935bdd799590c21fae' sent and included in block 'None'
310 0
Extrinsic '0x0f86fb0106c737a3d87d7d5bb0173b3100e7baddfd5d7631efe54ccac7143c2b' sent and included in block 'None'
QmUALZ8C4iffoMqQja5DedLuPS5j2ygD28npaaEinBa

Extrinsic '0xcb27bd888308985aff227386128bfd4e0ba7832353ed7ba4a4a1508c64a36340' sent and included in block 'None'
QmTGQgLz8TRAVXg2HVCLtQRoBQxKfLLCftNPuc5FhTG5YR
,
Extrinsic '0x9831cdcd2b43112153afff79d1c5e89393648ef41d251c5f89230518b2d453bd' sent and included in block 'None'
62320 0
Extrinsic '0xb5ff4f0b4685c3cbed2a868331382c663992382c201c45e7481820a5cc7ff4b8' sent and included in block 'None'
QmVcwGhaz8kCKMQHkkJVVEGbFs7kLLytZdZNe2pB2CrTMb

Extrinsic '0xa2fc92a217edb7419ac8b5b6b83cd0371bf2a5cf0d428da9cbd60c7497d656a6' sent and included in block 'None'
3996 0
Extrinsic '0xdd48a76cfb843cdc57af9abf405f5c42160309e78f466a6993169f17061461d8' sent and included in block 'None'
QmVvJ794kmaRGhrb8uXp5iVm6xo6oaHNJhBnp8p4xGrecd

Extrinsic '0xd6708c9bf161c83438689195f24a0dd6f80e6f47ed91d0f3d47638bf811ce038' sent and included in block 'None'
11945 0
Extrinsic '0x16e8a2a12d0d2c517113fe4b4d970bc7b0fbc8e67c1d0bd7ba2b1f7a5d1531b9' sent and included in block 'None'
QmcFuvVtbY3BNoKZncAGWGwyqrFzhzUpgYr8koSsc

Extrinsic '0xee5329ab73bd2e8dd431a57ae76c03233d401e742a6c7047bb0e5fd175736998' sent and included in block 'None'
QmVUCYxjczjEXjfPUC77koajPhy2HJzc4QdSA75VgmA9rP
,
Extrinsic '0x169677611b98aa354979f839ff051da138e2e9b9f7d09998741b7817dde3da43' sent and included in block 'None'
54423 0
Extrinsic '0x70a3152fa7cfd15533cb4ef09d52cc0c3cf53c93bc213d690530943fe00b77f7' sent and included in block 'None'
Qmb1Z2u5sHoLSCz6xLg9wNZrZKAkJg3jm5wfW81RMRq5nq

Extrinsic '0xd2851dcb0f12af395ab49537c79e9a2465cf36b605c3be807f2e074041a7c356' sent and included in block 'None'
4165 0
Extrinsic '0x8d1db7a2d67ce9361b2304899cf0af2230ec0770b4e0b5171c8dfeb829a51f54' sent and included in block 'None'
QmUJnQ1X6ZCztWoF2VFuwknwaYXfDvX4c23ezEZF1EhnSz

Extrinsic '0x8803491cc958771488a6726b9c7d0410da21ba25489cd581a5d693d2ca194f5a' sent and included in block 'None'
3098 0
Extrinsic '0xa06128e6b886f4e2e65123b045f03fa6e6bceac25abccf3f6952fe14fdb0add9' sent and included in block 'None'
QmaeWZU9mq5RkBSQkAkAAWCLv2Z2Ds5nt18n5U18G2

...

Extrinsic '0x5533bebab8cb2006114a11e27c28c44d98ce8440686de16612ec855ab64e0919' sent and included in block 'None'
QmZGwmQc23mBp3i4xEioKo8TcNaihbonQcc7v4dRFGMAky
,
Extrinsic '0x0fbaa4338f45f69e19e0928721cbab07f7acf48365db0bd80713f3746b6962bf' sent and included in block 'None'
23565 0
Extrinsic '0x507318e552b4b26b22d967b83615b0c5c1287257151cf45534a0929f720e6283' sent and included in block 'None'
QmaBEhCCA4oSmL9LaU578yWGdwGAEuETk61Jt17S5G94gB

Extrinsic '0x68e3d86adc818476b036e408cb1b6794614d799fbc728e55d65da1459a28d822' sent and included in block 'None'
931 0
Extrinsic '0xbc84109afcb00a41aae302eaac903a7921532bad64cab5cf9474596063803051' sent and included in block 'None'
QmSK3Q77zNAppxEGcvuPpJuxkBpByPYjHa7vLLXqUfGt5e

Extrinsic '0xb86ed63d131b756c812d8cab2021ae6da7cf03d057bb3c00c72390030d7f4687' sent and included in block 'None'
1335 0
Extrinsic '0xde6c1cb1251e57ce9f9166e9173cbb44df272ff1248d0bc2be02be51269434ad' sent and included in block 'None'
QmaPgnGhtBKkEbTR26ebZwAuqZabjD3ZgGWgkS9BFa2

Extrinsic '0x3ad15c1160e5d35c937523ebb20bfdb5ac341d704e2317e450b089f98cb7ee44' sent and included in block 'None'
QmUzwn9ZB25cK3Boyz8AakkrAq4dUUHnr3s2m4eCyhdHwU
,
Extrinsic '0x677b8bca25beff583f3949dfa664a3040cf0bd302c9e88eceddef0afadb63b5c' sent and included in block 'None'
23190 0
Extrinsic '0x761b827b51c57fce3c16ddcff931503c5b3d4eea404553c02db7ff9de1b8c23c' sent and included in block 'None'
QmcLMcG61tMtcxwgsKDk9pdLsFR94Y8gSobpwouiPWiHfG

Extrinsic '0x75df6948a269e21492b4bda3fe934197e2d66f1bc9967a9da394abb81ffee6fc' sent and included in block 'None'
1 0
Extrinsic '0x29477f39e3324372aac9615a054e6ec2a16974d3e2c472f818fd7a3720b8c3fb' sent and included in block 'None'
QmbVSaZcgJys6Ctr5cxvaZbNtib8ssGSEZNaVreutPZMGT

Extrinsic '0xc96d923095ed2e65dabd9820cd63432bae87247a600c6df8edfe16fbf1b8a1bd' sent and included in block 'None'
562 0
Extrinsic '0x6d300e8c3236ca4fbf6c996f28a1f8c8e6f895e0a69c9a0a289e8e09fb60f8d4' sent and included in block 'None'
QmY1E5GPoDMPNjjNAp1Z8QpPLUHiGrhq3hi3yGyUYg1NUR

Extrinsic '0xaf4e8e565d5e18aba8cb7183949b46559542ce40592c6ccbf088da99e1d73c84' sent and included in block 'None'
QmUZQFesZZp5jqBug9WrW5Rbkk4m4ZSVRj6C7a8TYnDc3W
,
Extrinsic '0x270ded4bce19fab2ef7239a8d50d8c99d12bfdf7fa3485bbf781bbd4c758938a' sent and included in block 'None'
22218 0
Extrinsic '0xbebec8b3c26de69977f083a27eb94a257f821c03e5a46494e449d2782894280a' sent and included in block 'None'
QmUkS7DgZUKtUMKzUZvD5RfuyZPGFCrvCSRSG1oYcJMjmv

Extrinsic '0xb88da00a7a75e031f88a36ee076bd28a02afe509b6c276b179a09036b8dfa6aa' sent and included in block 'None'
3763 0
Extrinsic '0x11aac7d247baff673f3b9ecb076c057e6db3c3c69a298dda0a5585f039285cfc' sent and included in block 'None'
QmaiZYp9H4SxH6uSH6sJyzFW1yyW3PU5RJZ2XNy3SrtLVV

Extrinsic '0xe7560734cea22ab410f3a78cfe2da69bf5dd7db8a9d9486bd28fe3720c68d206' sent and included in block 'None'
200 0
Extrinsic '0x517c2189833d17c18f26e3346ecb45884853f4805c939ff5479bfd2879527b4e' sent and included in block 'None'
QmcsBddmhSC3RtkGBcweumHRhR3cwYFuYMPVrpf2Z25

Extrinsic '0x151b6c224e73af62eeef4b1a8b83be559822be724443291bb9fbf2d29e35b9f8' sent and included in block 'None'
QmU4AysRYDrJzUkk48mfuE4whbdrdUbHL2vRzeGqQ6sqaA
,
Extrinsic '0xfe57055fb321242f45681e74669988ca5e3f317bcf8bf3a3a0eb4f9ab8d5d0b9' sent and included in block 'None'
21246 0
Extrinsic '0x4f12be2da654ba5c5f88093e145e46b10c7c44070fcc4016c9f8a59e2a7b5030' sent and included in block 'None'
QmUP5FM8A7KzHgSLiu667VYGmsKAgsqUJRZbz2yDbEs8Ma

Extrinsic '0x1e301727a9dd06025386f9e73de548d04712b0b7f2dd29384521754a2dd6911d' sent and included in block 'None'
7113 0
Extrinsic '0x47d5c6e21130e9bb81490951b1a3214f23ffb92b8d2da545caa6e0689ff5d04a' sent and included in block 'None'
Qmbvu4JAcXBmRPTAEubY75CAJDUdK35QuuVgoxqVgDidrC

Extrinsic '0x67644bce563d5183debdb48549375cce2370aebe8d6ccd4ab87a5e45011ceacf' sent and included in block 'None'
1091 0
Extrinsic '0x7752d20fb2421f50fd9f3c9b72ff1a64782ed7e2359e460d04b4e73b29a75641' sent and included in block 'None'
QmacR5EoKWsW3JWYzKYrkEKAEX6dFdxMhFQ4zr3nk5

Extrinsic '0x9d775d03fe4cf5fa5968c0c15b5303922d1d2a7020d4966e902acbca2ff4d7f7' sent and included in block 'None'
QmdiUULSdFzfknQHFd6TXiS7azE8eatrmw2pKeorAy4zF5
,
Extrinsic '0x64852b1f98eefb36c3ee61bf3c18db2c44998981e48cdf09158eee5bc8187c32' sent and included in block 'None'
20699 0
Extrinsic '0x359a6372d4c2766db61299e7da3c29663a1ebdb9506896ba7f893dff120ae9b6' sent and included in block 'None'
QmWULxKr69JgwCxbujRfdWyWi43rmWvLMe3ZzZx5KvLGMX

Extrinsic '0x9473e349d020499eff0110c9168efc4394e06aec2625074a659b3b4c006a173c' sent and included in block 'None'
1 0
Extrinsic '0xe493c7d03a59b5202768523adedf7caaf120c468250cd5f4d8616d0b8f6c6225' sent and included in block 'None'
QmXJC8EmDjAVLGHhWDFjo1SmiE5jX5214xSMUERdP1uiWo

Extrinsic '0x79e6954590645b6243173f5bde69709640c4cc1340c0586cdd8fe0db35ac4bb1' sent and included in block 'None'
478 0
Extrinsic '0x8ba2bb4f0c558d5efb5b3847b0d8936c0dac656d26bcde58efbdbf2b1e99ed1d' sent and included in block 'None'
QmaxiVLAVz1pVWDL1LDtcKAPbP9BpZWCfafLdRMdP6PERn

In [ ]:
import get_top_posts from res

In [509]:
[post_schemaId, postcomment_schemaId, commentcomment_schemaId, postvote_schemaId, commentvote_schemaId]

[147, 150, 151, 154, 153]

In [515]:
substrate.get_block()['header']['number']

5496

In [489]:
start_block = 5490

In [490]:
content_json = {}
for schemaId in [post_schemaId, postcomment_schemaId, commentcomment_schemaId, postvote_schemaId, commentvote_schemaId]:
    params = [
        schemaId,
        {
            "page_size": 10000,
            "from_block": start_block,
            "to_block": 10000,
            "from_index": 0,
        }
    ]

    content_json[schemaId] = substrate.rpc_request(
        method='messages_getBySchema',
        params=params,
    )['result']['content']

In [496]:
content_json[post_schemaId]

[{'block_number': 5389,
  'data': '0x2c6d6f766965732c516d5550564d337a31516665636354486f416e6e57437a4763356966394d474e4b625251454d6f6d796b6b4d4c72',
  'index': 0,
  'msa_id': 1,
  'signer': '5FHneW46xGXgs5mUiveU4sbTyGBzmstUspZC92UhjJM694ty'},
 {'block_number': 5389,
  'data': '0x2c53616e64657273466f72507265736964656e742c516d5738364173537a39674b6648427067545a696b6766426146483167594338723147504b6d325044726f747446',
  'index': 2,
  'msa_id': 1,
  'signer': '5FHneW46xGXgs5mUiveU4sbTyGBzmstUspZC92UhjJM694ty'},
 {'block_number': 5391,
  'data': '0x2c53616e64657273466f72507265736964656e742c516d5738364173537a39674b6648427067545a696b6766426146483167594338723147504b6d325044726f747446',
  'index': 0,
  'msa_id': 1,
  'signer': '5FHneW46xGXgs5mUiveU4sbTyGBzmstUspZC92UhjJM694ty'},
 {'block_number': 5391,
  'data': '0x2c6177772c516d5731646b454e70674e32393357506855373959395645414b6d68386a6f596232485270445077615670667132',
  'index': 22,
  'msa_id': 1,
  'signer': '5FHneW46xGXgs5mUiveU4sbTyGBzmstUspZC9

In [495]:
len(content_json[post_schemaId])

86

In [505]:
num_posts = 100
page_number = 1

posts = {}
    
for content in content_json[postvote_schemaId]:
    data = bytes.fromhex(content['data'][2:]).decode().split(',')
    if data[1] not in posts:
        posts[data[1]] = {'upvotes': 0, 'downvotes': 0, 'score': 0}
    if data[1] in posts:
        num_votes = int(data[2])
        posts[data[1]]['score'] += num_votes 
        if num_votes > 0:
            posts[data[1]]['upvotes'] += num_votes
        else:
            posts[data[1]]['downvotes'] += -1*num_votes  
            
posts = OrderedDict(sorted(posts.items(), key=lambda t: t[1]['score'], reverse=True))
i_range = list(range((page_number - 1) * num_posts, page_number * num_posts))
posts = {k: v for i, (k,v) in enumerate(posts.items()) if i in i_range}

i = 0
for content in reversed(content_json[post_schemaId]):
    if i == len(posts):
        break
        
    data = bytes.fromhex(content['data'][2:]).decode().split(',')
    if data[2] not in posts:
        continue
        
    i += 1
    posts[data[2]].update(json.loads(client.cat(data[2]).decode()))
    

posts_list = []
for i, (k,v) in enumerate(posts.items()):
    if i in i_range:
        v['id'] = k
        posts_list.append(v)
    

In [506]:
posts_list

[{'upvotes': 262443,
  'downvotes': 0,
  'score': 262443,
  'category': 'SandersForPresident',
  'username': 'Smartercow',
  'profile_pic': 'https://www.redditstatic.com/avatars/defaults/v2/avatar_default_2.png',
  'title': 'Sanders message to Fox News viewers',
  'body': '',
  'url': 'https://v.redd.it/mzq6430t9n591',
  'is_nsfw': False,
  'id': 'QmW86AsSz9gKfHBpgTZikgfBaFH1gYC8r1GPKm2PDrottF'},
 {'upvotes': 125027,
  'downvotes': 0,
  'score': 125027,
  'category': 'aww',
  'username': 'elphaba16',
  'profile_pic': 'https://styles.redditmedia.com/t5_so8ka/styles/profileIcon_snoo27eb7eac-9ca8-4c84-878d-36b144570655-headshot.png?width=256&height=256&crop=256:256,smart&s=53825fc21a7bbf38b2e49190bef52bfa4c8fc747',
  'title': 'A video analysis of the difference between Joule joining Kelvin and Kelvin joining Joule.',
  'body': '',
  'url': 'https://v.redd.it/u4ozvjcd5s591',
  'is_nsfw': False,
  'id': 'QmW1dkENpgN293WPhU79Y9VEAKmh8joYb2HRpDPwaVpfq2'},
 {'upvotes': 96795,
  'downvotes': 0,

In [503]:
i, len(posts)

(84, 84)

In [504]:
posts

{'QmW86AsSz9gKfHBpgTZikgfBaFH1gYC8r1GPKm2PDrottF': {'upvotes': 262443,
  'downvotes': 0,
  'score': 262443,
  'category': 'SandersForPresident',
  'username': 'Smartercow',
  'profile_pic': 'https://www.redditstatic.com/avatars/defaults/v2/avatar_default_2.png',
  'title': 'Sanders message to Fox News viewers',
  'body': '',
  'url': 'https://v.redd.it/mzq6430t9n591',
  'is_nsfw': False},
 'QmW1dkENpgN293WPhU79Y9VEAKmh8joYb2HRpDPwaVpfq2': {'upvotes': 125027,
  'downvotes': 0,
  'score': 125027,
  'category': 'aww',
  'username': 'elphaba16',
  'profile_pic': 'https://styles.redditmedia.com/t5_so8ka/styles/profileIcon_snoo27eb7eac-9ca8-4c84-878d-36b144570655-headshot.png?width=256&height=256&crop=256:256,smart&s=53825fc21a7bbf38b2e49190bef52bfa4c8fc747',
  'title': 'A video analysis of the difference between Joule joining Kelvin and Kelvin joining Joule.',
  'body': '',
  'url': 'https://v.redd.it/u4ozvjcd5s591',
  'is_nsfw': False},
 'QmWoqmQpunMdgR7GsHCinfDRWoeYUx9hy83KnSMdw4Bynd': {'

In [395]:
schema_count = substrate.query(
    module='Schemas',
    storage_function='SchemaCount',
    params=[]
).value

post_schemas = {}
for i in range(1, schema_count+1):
    schemaTemp = substrate.query(
        module='Schemas',
        storage_function='Schemas',
        params=[i]
    )
    print(schemaTemp.value)

username,profile_pic
pics,QmVbFm5mNfgk1o4e6tuhRDrygWhynnabq9aQfcZSW42RPY,parent_hash,data_hash
wallstreetbets,QmYwaTsoKb6jF8y5AGresVKj5LzypWZPWGwyzyeSgVYjy4,parent_hash,data_hash
news,QmZRYUyrppGsDPDB2Q9wqyfJAtPkWKbTkSs9FasxGLpvi7,parent_hash,data_hash
movies,QmdfkFFtwxGyZaLw7teURyuxGmzpPxLjZrUYSYUfT874VL,parent_hash,data_hash
funny,Qmf943KpByMd3Bz6j2QG4CppVHgG2SV93u7wzHwyiMGVVL,parent_hash,data_hash
wallstreetbets,QmdZZ1RcE7z8eiqS4e687qm9gbsGZBsAGYsbpBr1xMsMyv,parent_hash,data_hash
memes,QmUm4yRmjbgyjeeKukuGPkYiZJRB1KeR9J1u7vWLus9j2w,parent_hash,data_hash
funny,QmTLrPfhVysDXEsUZdqz7GYZ6xF1Xy7FL7SUDeb2SxaejQ,parent_hash,data_hash
aww,QmUJxZmYJhZDoJFS1vcEv86kXtjN1rSym9Ywh7QtfBLzZC,parent_hash,data_hash
wallstreetbets,QmYpWJBnpnyZmvQpp4XyHtbtnKLP9VG9hwUchUmrXTwMq6,parent_hash,data_hash
pics,Qmd8ZYMiWohnEpEW2SQjTsFJZaj1HfnBeUENBkM4hAqASV,parent_hash,data_hash
memes,QmRcBBbh54LN1tVzjX4aKC6skNPgC8rj1sup3SkLWZSLwr,parent_hash,data_hash
gaming,QmZsjUdDvXffGETG6oVAwtJFRs7jmnG4vaFRbpP1sRn9HD,pa

In [349]:
post_pattern = re.compile(f".*,.*,parent_hash,data_hash")

In [350]:
schema_count = substrate.query(
    module='Schemas',
    storage_function='SchemaCount',
    params=[]
).value

post_schemas = {}
for i in range(1, schema_count+1):
    schemaTemp = substrate.query(
        module='Schemas',
        storage_function='Schemas',
        params=[i]
    )
    if post_pattern.match(schemaTemp.value):
        print(schemaTemp.value)
        post_schemas[schemaTemp.value] = i

pics,QmVbFm5mNfgk1o4e6tuhRDrygWhynnabq9aQfcZSW42RPY,parent_hash,data_hash
wallstreetbets,QmYwaTsoKb6jF8y5AGresVKj5LzypWZPWGwyzyeSgVYjy4,parent_hash,data_hash
news,QmZRYUyrppGsDPDB2Q9wqyfJAtPkWKbTkSs9FasxGLpvi7,parent_hash,data_hash
movies,QmdfkFFtwxGyZaLw7teURyuxGmzpPxLjZrUYSYUfT874VL,parent_hash,data_hash
funny,Qmf943KpByMd3Bz6j2QG4CppVHgG2SV93u7wzHwyiMGVVL,parent_hash,data_hash
wallstreetbets,QmdZZ1RcE7z8eiqS4e687qm9gbsGZBsAGYsbpBr1xMsMyv,parent_hash,data_hash
memes,QmUm4yRmjbgyjeeKukuGPkYiZJRB1KeR9J1u7vWLus9j2w,parent_hash,data_hash
funny,QmTLrPfhVysDXEsUZdqz7GYZ6xF1Xy7FL7SUDeb2SxaejQ,parent_hash,data_hash
aww,QmUJxZmYJhZDoJFS1vcEv86kXtjN1rSym9Ywh7QtfBLzZC,parent_hash,data_hash
wallstreetbets,QmYpWJBnpnyZmvQpp4XyHtbtnKLP9VG9hwUchUmrXTwMq6,parent_hash,data_hash
pics,Qmd8ZYMiWohnEpEW2SQjTsFJZaj1HfnBeUENBkM4hAqASV,parent_hash,data_hash
memes,QmRcBBbh54LN1tVzjX4aKC6skNPgC8rj1sup3SkLWZSLwr,parent_hash,data_hash
gaming,QmZsjUdDvXffGETG6oVAwtJFRs7jmnG4vaFRbpP1sRn9HD,parent_hash,data_hash
g

In [363]:
substrate.get_block()['header']['number']

In [364]:
b['header']['number']

5123

In [287]:
b.keys()

dict_keys(['extrinsics', 'header'])

In [361]:
%%time
content_jsons = {}
for schema, schemaId in post_schemas.items():
    params = [
        schemaId,
        {
            "page_size": 10000,
            "from_block": 5123,
            "to_block": 10000,
            "from_index": 0,
        }
    ]

    content = substrate.rpc_request(
        method='messages_getBySchema',
        params=params,
    )
    if len(content['result']['content']) > 0:
        content_jsons[schema] = content['result']['content']

CPU times: user 276 ms, sys: 7.44 ms, total: 283 ms
Wall time: 11.5 s


In [362]:
len(content_jsons)

116

In [353]:
def add_comment(_data, _dict, _is_vote):
    for hsh in _dict.keys():
        if hsh == data[2]:
            if is_vote:
                if '-' in data[3]:
                    # downvote
                    _dict['data']['downvotes'] += data[3]
                else:
                    # upvote
                    _dict['data']['upvotes'] += data[3]
            else:
                _dict[data[3]] = {
                    'data': json.loads(client.cat(_data).decode()), 
                    'comments': {}
                }
                
                _dict['data'].update({"upvotes": 0, "downvotes": 0})
            return True
        result = add_comment(_data, _dict['comments'], _is_vote)
        if result:
            return True
    return False

In [354]:
posts = {}
for schema, contents in content_jsons.items():
    schema_items = schema.split(',')
    category = schema_items[0]
    post_hash = schema_items[1]
    posts[post_hash] = {'data': {"upvotes": 0, "downvotes": 0}, 'comments': {}}
    
    for content in contents:
        data = bytes.fromhex(content['data'][2:]).decode().split(',')
        # votes had numeric numbers instead of hashes
        is_vote = data[3].strip('-').isnumeric() 
        if is_vote:
            data[3] = int(data[3])
            
        if data[2] == '': 
            # empty means its post data
            posts[post_hash]['data'].update(json.loads(client.cat(data[3]).decode()))
        elif data[2] == post_hash: 
            # post_hash means its comment
            if is_vote:
                if data[3] < 0:
                    # downvote
                    posts[post_hash]['data']['downvotes'] += data[3]
                else:
                    # upvote
                    posts[post_hash]['data']['upvotes'] += data[3]
            else:
                posts[post_hash]['comments'][data[3]] = {
                    'data': json.loads(client.cat(data[3]).decode()), 
                    'comments': {}
                }
                posts[post_hash]['comments'][data[3]]['data'].update({"upvotes": 0, "downvotes": 0})
        else: 
            # neither means its comment of comment
            result = add_comment(data[3], posts[post_hash]['comments'], is_vote)
            if not result:
                print('couldnt find', data[2], json.loads(client.cat(data[3]).decode()))

In [355]:
from collections import OrderedDict
o = OrderedDict(sorted(posts.items(), key=lambda t: t[1]['data']['upvotes'], reverse=True))

In [356]:
o.items()

odict_items([('QmT2Zo15TiDYGqfmXAmYkMGkf4WMY8sdQGiNsZsHAtuYnN', {'data': {'upvotes': 1167863, 'downvotes': 0, 'category': 'wallstreetbets', 'username': 'SomeGuyInDeutschland', 'profile_pic': 'https://styles.redditmedia.com/t5_bcx7b/styles/profileIcon_snoo908b3c30-edde-42cf-b40d-83391a012cb0-headshot-f.png?width=256&height=256&crop=256:256,smart&s=98c80967daec2a3af329ef021215bf076e0456e3', 'title': 'Times Square right now', 'body': '', 'url': 'https://v.redd.it/x64z70f7eie61', 'is_nsfw': False}, 'comments': {'QmTcQ8sFZPCn4Hp9TAgq2Uwi8Cbo6UZAGktyMvN3U4dnxL': {'data': {'parent_hash': 'QmT2Zo15TiDYGqfmXAmYkMGkf4WMY8sdQGiNsZsHAtuYnN', 'username': 'SomeGuyInDeutschland', 'profile_pic': 'https://styles.redditmedia.com/t5_bcx7b/styles/profileIcon_snoo908b3c30-edde-42cf-b40d-83391a012cb0-headshot-f.png?width=256&height=256&crop=256:256,smart&s=98c80967daec2a3af329ef021215bf076e0456e3', 'body': 'Someone needs to open a GameStop across the ny stock exchange 💎🙌', 'upvotes': 0, 'downvotes': 0}, 'co

In [357]:
posts_list = []
for k, v in OrderedDict(sorted(posts.items(), key=lambda t: t[1]['data']['upvotes'], reverse=True)).items():
    posts_list.append({k:v})

In [358]:
posts_list

[{'QmT2Zo15TiDYGqfmXAmYkMGkf4WMY8sdQGiNsZsHAtuYnN': {'data': {'upvotes': 1167863,
    'downvotes': 0,
    'category': 'wallstreetbets',
    'username': 'SomeGuyInDeutschland',
    'profile_pic': 'https://styles.redditmedia.com/t5_bcx7b/styles/profileIcon_snoo908b3c30-edde-42cf-b40d-83391a012cb0-headshot-f.png?width=256&height=256&crop=256:256,smart&s=98c80967daec2a3af329ef021215bf076e0456e3',
    'title': 'Times Square right now',
    'body': '',
    'url': 'https://v.redd.it/x64z70f7eie61',
    'is_nsfw': False},
   'comments': {'QmTcQ8sFZPCn4Hp9TAgq2Uwi8Cbo6UZAGktyMvN3U4dnxL': {'data': {'parent_hash': 'QmT2Zo15TiDYGqfmXAmYkMGkf4WMY8sdQGiNsZsHAtuYnN',
      'username': 'SomeGuyInDeutschland',
      'profile_pic': 'https://styles.redditmedia.com/t5_bcx7b/styles/profileIcon_snoo908b3c30-edde-42cf-b40d-83391a012cb0-headshot-f.png?width=256&height=256&crop=256:256,smart&s=98c80967daec2a3af329ef021215bf076e0456e3',
      'body': 'Someone needs to open a GameStop across the ny stock exchang

In [305]:
dict(sorted(posts.items()))

{'QmPFmSNa1kmQLR4tYwJG5DuJC4HiBNnfu3vHw8tUCjR8xr': {'data': {'upvotes': 70712,
   'downvotes': 0},
  'comments': {'Qmb7ukkEQ3jPXgVnVC5F1JNQmWvCJxC2jYYhHzansj6c5Z': {'data': {'parent_hash': 'QmPFmSNa1kmQLR4tYwJG5DuJC4HiBNnfu3vHw8tUCjR8xr',
     'username': 'ReallyRickAstley',
     'profile_pic': 'https://www.redditstatic.com/avatars/defaults/v2/avatar_default_4.png',
     'body': 'For a second I thought this was /r/OldSchoolCool and was thinking ‘Wow, he looks just like Rick Astley’',
     'upvotes': 0,
     'downvotes': 0},
    'comments': {}},
   'QmacZuUZnTEvJEiYT2AF7TiS7v4Y2EicYWS5TyH6W9d5FU': {'data': {'parent_hash': 'QmPFmSNa1kmQLR4tYwJG5DuJC4HiBNnfu3vHw8tUCjR8xr',
     'username': 'ReallyRickAstley',
     'profile_pic': 'https://www.redditstatic.com/avatars/defaults/v2/avatar_default_4.png',
     'body': "A reminder that Rick gave the best AMA answer ever a few years back. [No it's not a rickroll.](https://www.reddit.com/r/Music/comments/56cdgm/ama_im_really_rick_astley_i_swear_a

In [272]:
data

['', '', 'QmQeMR1Zvx14bHU1M19a85MDrhQCVuU1Y8jWZLYi8v5kbH', 0]

In [260]:
s = '-352'

In [264]:
s.strip('-').isnumeric()

True